# Example with optional parameters
Toargridding has a number of required arguments for a dataset. Those include the time range, variable and statistical analysis. The TAOR-DB has a large number of metadata fileds that can be used to further refine this request.
A python dictionary can be provided to include theses other fields. The analysis service provides an error message, if the requested parameters does not exist (check for typos) or if the provided value is wrong.

In this example we want to obtain data from 2000 to 2018 (maybe change this, if you want your results faster:-)).

The fist block contains the includes and the setup of the logging.

In [ ]:
from datetime import datetime as dt
from collections import namedtuple
from pathlib import Path

from toargridding.toar_rest_client import AnalysisServiceDownload, Connection
from toargridding.grids import RegularGrid
from toargridding.gridding import get_gridded_toar_data
from toargridding.metadata import TimeSample

We now want to include packages for logging. We want so see some output in the shell, we want to log exceptions and we maybe want to have a logfile to review everything later:

In [ ]:

import logging
from toargridding.defaultLogging import toargridding_defaultLogging

#setup of logging
logger = toargridding_defaultLogging()
logger.addShellLogger(logging.DEBUG)
logger.logExceptions()
logger.addRotatingLogFile(Path("log/produce_data_withOptional.log"))#we need to explicitly set a logfile
#logger.addSysLogger(logging.DEBUG)

## Preparation of requests
in the next block we prepare the request to the analysis service.
The dictionary details4Query adds additional requirements to the request. Here, the two fields *toar1_category* and *type_of_area* are used. Both stand for a classification of stations depending on the surrounding area. It is advised to use only one at once. 


moreOptions is implemented as a dict to add additional arguments to the query to the REST API
For example the field *toar1_category* with its possible values Urban, RuralLowElevation, RuralHighElevation and Unclassified can be added 
(see page 18 in https://toar-data.fz-juelich.de/sphinx/TOAR_UG_Vol03_Database/build/latex/toardatabase--userguide.pdf).
Or *type_of_area* with urban, suburban and rural on page 20 can be used.

There are a many more metadata available in the user guide, feel free to look around.

In [ ]:
#creation of request.
# helper to keep the configuration together
Config = namedtuple("Config", ["grid", "time", "variables", "stats","moreOptions"])

#uncomment, what you want to test:-)
details4Query ={
    #"toar1_category" : "Urban" #uncomment if wished:-)
    #"toar1_category" : "RuralLowElevation" #uncomment if wished:-)
    #"toar1_category" : "RuralHighElevation" #uncomment if wished:-)
    #"type_of_area" : "Urban" #also test Rural, Suburban,
    "type_of_area" : "Rural" #also test Rural, Suburban,
    #"type_of_area" : "Suburban" #also test Rural, Suburban,
}

#a regular grid with 1.9°x2.5° resolution. A warning will be issued as 1.9° does not result in  natural number of grid cells.
grid = RegularGrid( lat_resolution=1.9, lon_resolution=2.5, )

configs = dict()

# we split the request into one request per year.
##for educational reasons the extraction of only two years is fine:-)
#for year in range(0,19):
for year in range(0,2):
    valid_data = Config(
        grid,
        TimeSample( start=dt(2000+year,1,1), end=dt(2000+year,12,31), sampling="daily"),#possibly adopt range:-)
        #TimeSample( start=dt(2000+year,1,1), end=dt(2000+year,12,31), sampling="monthly"),#possibly adopt range:-)
        ["mole_fraction_of_ozone_in_air"],#variable name
        #[ "mean", "dma8epax"],# will start one request after another other...
        [ "dma8epa_strict" ],
        #[ "mean" ],
        details4Query
    )
    
    configs[f"test_ta{year}"] = valid_data


We now need to setup the out connection to the analysis service of the TOAR database. We also setup directories to store the data.

In [ ]:
stats_endpoint = "https://toar-data.fz-juelich.de/api/v2/analysis/statistics/"
cache_basepath = Path("cache")
result_basepath = Path("results")
cache_basepath.mkdir(exist_ok=True)
result_basepath.mkdir(exist_ok=True)
analysis_service = AnalysisServiceDownload(stats_endpoint=stats_endpoint, cache_dir=cache_basepath, sample_dir=result_basepath, use_downloaded=True)

## Download and gridding:
Now we come to the last step: we want to download the data, process them and store them to disc.

CAVE: this cell runs about 45minutes per requested year. therefore we increase the waiting duration to 1h per request.
the processing is done on the server of the TOAR database.
A restart of the cell continues the request to the REST API. Data are cached on the local computer to prevent repetitive downloads.
The download can also take a few minutes

In [ ]:

# maybe adopt the interval for requesting the results and the total duration, before the client pauses the requests.
# as the requests take about 45min, it is more suitable to wait 60min before timing out the requests than the original 30min.
analysis_service.connection.set_request_times(interval_min=5, max_wait_minutes=60)

for person, config in configs.items():
    print(f"\nProcessing {person}:")
    print(f"--------------------")
    datasets, metadatas = get_gridded_toar_data(
        analysis_service=analysis_service,
        grid=config.grid,
        time=config.time,
        variables=config.variables,
        stats=config.stats,
        contributors_path=result_basepath,
        **config.moreOptions
    )

    for dataset, metadata in zip(datasets, metadatas):
        dataset.to_netcdf(result_basepath / f"{metadata.get_id()}_{config.grid.get_id()}.nc")
        print(metadata.get_id())